In [1]:
from selenium import webdriver
from selenium.common.exceptions import TimeoutException
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By
from webdriver_manager.chrome import ChromeDriverManager
from progressbar import *   
import time 
import numpy as np
import pandas as pd
import os
import datetime
from selenium.webdriver.chrome.options import Options

In [2]:
start_str="1990-01-01"
end_str="2021-04-23"
start = datetime.datetime.strptime(start_str, "%Y-%m-%d")
end = datetime.datetime.strptime(end_str, "%Y-%m-%d")
df=pd.DataFrame()
file_name=f"C:\\Users\\Chike\\Documents\\Projects\\weather_repo\\data\\raw\\1.0_Montreal_{start_str}_{end_str}.pkl"
file_name
# df.to_excel()

'C:\\Users\\Chike\\Documents\\Projects\\weather_repo\\data\\raw\\1.0_Montreal_1990-01-01_2021-04-23.pkl'

In [3]:
# %%capture
date_array = (start + datetime.timedelta(days=x) for x in range(0, (end-start).days))
 
dates_list=[date_object.strftime("%Y-%m-%d") for date_object in date_array]
weather_df=pd.DataFrame()
widgets = ['Test: ', Percentage(), ' ', Bar(marker='0',left='[',right=']'),
           ' ', ETA(), ' ', FileTransferSpeed()] #see docs for other options
nb_days=(end-start).days
pbar = ProgressBar(widgets=widgets, maxval=nb_days)
pbar.start()
for dates in dates_list:
    year=datetime.datetime.strptime(dates, "%Y-%m-%d").year
    month=datetime.datetime.strptime(dates, "%Y-%m-%d").month
    day=datetime.datetime.strptime(dates, "%Y-%m-%d").day
    days_since_start=(datetime.datetime.strptime(dates, "%Y-%m-%d")-start).days
    chrome_options = Options()
    chrome_options.headless = True
    chrome_options.add_argument("--log-level=3")
    
    pbar.update(days_since_start) #this adds a little symbol at each iteration

    print(dates)
    try:
        driver = webdriver.Chrome(ChromeDriverManager().install(),chrome_options=chrome_options);
        driver.get(f"https://www.wunderground.com/history/daily/ca/montreal/CYUL/date/{year}-{month}-{day}")
    except:
        continue
#     time.sleep(10)
    x_path='//*[@id="inner-content"]/div[2]/div[1]/div[5]/div[1]/div/lib-city-history-observation/div/div[2]/table'
    timeout = 30
    try:
        element_present = EC.presence_of_element_located((By.XPATH,x_path))
        WebDriverWait(driver, timeout).until(element_present)
    except TimeoutException:
        print(f"Timed out waiting for page to load: {year}-{month}-{day}")
    tbl = driver.find_element_by_xpath(x_path).get_attribute('outerHTML')
    driver.close()
    driver.quit()
    df=pd.read_html(tbl)[0].dropna(axis = 0, subset = ['Humidity'])
    df.columns = df.columns.str.replace(' ', '_')
    df['Temperature_Fahrenheit']=df.Temperature.str.extract('(\d+)')
    df['Dew_Point_Fahrenheit']=df.Dew_Point.str.extract('(\d+)')
    df['Humidity_Float']=df.Humidity.str.extract('(\d+)').astype(int)/100
    df['Wind_Speed_MPH']=df.Wind_Speed.str.extract('(\d+)')
    df['Wind_Gust_MPH']=df.Wind_Gust.str.extract('(\d+)')
    df['Pressure_IN']=df.Pressure.str.extract('(\d+)')
    df['Precip_IN']=df['Precip.'].str.extract('(\d+)')
    df['Time_Clean']=pd.to_datetime(df.Time, format='%I:%M %p').dt.time
    df=df[pd.to_datetime(df.Time_Clean,format='%H:%M:%S').dt.minute==0]
    df['Date']=dates
    final_df=df.drop(['Temperature','Dew_Point','Humidity','Wind_Speed','Wind_Gust','Pressure','Precip.'],axis=1)
    weather_df=pd.concat([weather_df,final_df])#.reset_index(drop=True)
pbar.finish()
weather_df

Test:   0% [                                       ] ETA:  --:--:--   0.00  B/s

====== WebDriver manager ======
Current google-chrome version is 90.0.4430
Get LATEST driver version for 90.0.4430
Driver [C:\Users\Chike\.wdm\drivers\chromedriver\win32\90.0.4430.24\chromedriver.exe] found in cache
C:\Users\Chike\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: DeprecationWarning: use options instead of chrome_options


1990-01-01


Test:   0% [                                 ] ETA:  1 day, 4:54:21   0.11  B/s

====== WebDriver manager ======
Current google-chrome version is 90.0.4430
Get LATEST driver version for 90.0.4430
Driver [C:\Users\Chike\.wdm\drivers\chromedriver\win32\90.0.4430.24\chromedriver.exe] found in cache


1990-01-02


Test:   0% [                                       ] ETA:  23:28:34   0.14  B/s

====== WebDriver manager ======
Current google-chrome version is 90.0.4430
Get LATEST driver version for 90.0.4430
Driver [C:\Users\Chike\.wdm\drivers\chromedriver\win32\90.0.4430.24\chromedriver.exe] found in cache


...

Test:  32% [000000000000                           ] ETA:  13:41:04   0.16  B/s

====== WebDriver manager ======
Current google-chrome version is 90.0.4430
Get LATEST driver version for 90.0.4430
Driver [C:\Users\Chike\.wdm\drivers\chromedriver\win32\90.0.4430.24\chromedriver.exe] found in cache


2000-02-22


Test:  32% [000000000000                           ] ETA:  13:40:58   0.16  B/s

====== WebDriver manager ======
Current google-chrome version is 90.0.4430
Get LATEST driver version for 90.0.4430
Driver [C:\Users\Chike\.wdm\drivers\chromedriver\win32\90.0.4430.24\chromedriver.exe] found in cache


2000-02-23
Timed out waiting for page to load: 2000-2-23


NoSuchElementException: Message: no such element: Unable to locate element: {"method":"xpath","selector":"//*[@id="inner-content"]/div[2]/div[1]/div[5]/div[1]/div/lib-city-history-observation/div/div[2]/table"}
  (Session info: headless chrome=90.0.4430.85)


In [4]:
weather_df

Time Wind       Condition Temperature_Fahrenheit Dew_Point_Fahrenheit  \
0    1:00 AM    S          Cloudy                     36                   36   
2    2:00 AM   SW          Cloudy                     38                   38   
3    3:00 AM  SSW  Cloudy / Windy                     37                   34   
5    4:00 AM   SW  Cloudy / Windy                     36                    0   
7    5:00 AM   SW  Cloudy / Windy                     36                    0   
..       ...  ...             ...                    ...                  ...   
7    8:00 AM  NNE   Mostly Cloudy                     16                   10   
8    9:00 AM  NNE   Partly Cloudy                     16                   12   
9   10:00 AM  NNE            Fair                     18                   12   
10  11:00 AM  NNE            Fair                     21                   14   
11  12:00 PM  NNE            Fair                     23                   18   

    Humidity_Float Wind_Speed_MPH Wind_Gust_MPH Pressure_IN Precip_IN  \
0             1.00              6             0          29         0   
2             0.97             13             0          29         0   
3             0.87             29            35          29         0   
5             0.87             23             0          29         0   
7             0.87             21            31          29         0   
..             ...            ...           ...         ...       ...   
7             0.79              8             0          30         0   
8             0.86             10             0          30         0   
9             0.79             13             0          30         0   
10            0.74             10             0          30         0   
11            0.80              8             0          30         0   

   Time_Clean        Date  
0    01:00:00  1990-01-01  
2    02:00:00  1990-01-01  
3    03:00:00  1990-01-01  
5    04:00:00  1990-01-01  
7    05:00:00  1990-01-01  
..        ...         ...  
7    08:00:00  2000-02-22  
8    09:00:00  2000-02-22  
9    10:00:00  2000-02-22  
10   11:00:00  2000-02-22  
11   12:00:00  2000-02-22  

[87608 rows x 12 columns]

In [6]:
# %%capture
start_str="2000-2-23"
end_str="2021-04-23"
start = datetime.datetime.strptime(start_str, "%Y-%m-%d")
end = datetime.datetime.strptime(end_str, "%Y-%m-%d")

date_array = (start + datetime.timedelta(days=x) for x in range(0, (end-start).days))
 
dates_list=[date_object.strftime("%Y-%m-%d") for date_object in date_array]
widgets = ['Test: ', Percentage(), ' ', Bar(marker='0',left='[',right=']'),
           ' ', ETA(), ' ', FileTransferSpeed()] #see docs for other options
nb_days=(end-start).days
pbar = ProgressBar(widgets=widgets, maxval=nb_days)
pbar.start()
for dates in dates_list:
    year=datetime.datetime.strptime(dates, "%Y-%m-%d").year
    month=datetime.datetime.strptime(dates, "%Y-%m-%d").month
    day=datetime.datetime.strptime(dates, "%Y-%m-%d").day
    days_since_start=(datetime.datetime.strptime(dates, "%Y-%m-%d")-start).days
    chrome_options = Options()
    chrome_options.headless = True
    chrome_options.add_argument("--log-level=3")
    
    pbar.update(days_since_start) #this adds a little symbol at each iteration

    print(dates)
    try:
        driver = webdriver.Chrome(ChromeDriverManager().install(),chrome_options=chrome_options);
        driver.get(f"https://www.wunderground.com/history/daily/ca/montreal/CYUL/date/{year}-{month}-{day}")
    except:
        continue
#     time.sleep(10)
    x_path='//*[@id="inner-content"]/div[2]/div[1]/div[5]/div[1]/div/lib-city-history-observation/div/div[2]/table'
    timeout = 30
    try:
        element_present = EC.presence_of_element_located((By.XPATH,x_path))
        WebDriverWait(driver, timeout).until(element_present)
        tbl = driver.find_element_by_xpath(x_path).get_attribute('outerHTML')
    except TimeoutException:
        print(f"Timed out waiting for page to load: {year}-{month}-{day}")
    driver.close()
    driver.quit()
    df=pd.read_html(tbl)[0].dropna(axis = 0, subset = ['Humidity'])
    df.columns = df.columns.str.replace(' ', '_')
    df['Temperature_Fahrenheit']=df.Temperature.str.extract('(\d+)')
    df['Dew_Point_Fahrenheit']=df.Dew_Point.str.extract('(\d+)')
    df['Humidity_Float']=df.Humidity.str.extract('(\d+)').astype(int)/100
    df['Wind_Speed_MPH']=df.Wind_Speed.str.extract('(\d+)')
    df['Wind_Gust_MPH']=df.Wind_Gust.str.extract('(\d+)')
    df['Pressure_IN']=df.Pressure.str.extract('(\d+)')
    df['Precip_IN']=df['Precip.'].str.extract('(\d+)')
    df['Time_Clean']=pd.to_datetime(df.Time, format='%I:%M %p').dt.time
    df=df[pd.to_datetime(df.Time_Clean,format='%H:%M:%S').dt.minute==0]
    df['Date']=dates
    final_df=df.drop(['Temperature','Dew_Point','Humidity','Wind_Speed','Wind_Gust','Pressure','Precip.'],axis=1)
    weather_df=pd.concat([weather_df,final_df])#.reset_index(drop=True)
pbar.finish()
weather_df

Test:   0% [                                       ] ETA:  --:--:--   0.00  B/s

====== WebDriver manager ======
Current google-chrome version is 90.0.4430
Get LATEST driver version for 90.0.4430
Driver [C:\Users\Chike\.wdm\drivers\chromedriver\win32\90.0.4430.24\chromedriver.exe] found in cache
C:\Users\Chike\Anaconda3\lib\site-packages\ipykernel_launcher.py:28: DeprecationWarning: use options instead of chrome_options


2000-02-23
Timed out waiting for page to load: 2000-2-23


Test:   0% [                               ] ETA:  3 days, 11:13:03   0.03  B/s

====== WebDriver manager ======
Current google-chrome version is 90.0.4430
Get LATEST driver version for 90.0.4430
Driver [C:\Users\Chike\.wdm\drivers\chromedriver\win32\90.0.4430.24\chromedriver.exe] found in cache


2000-02-24
Timed out waiting for page to load: 2000-2-24


Test:   0% [                                ] ETA:  3 days, 8:20:59   0.03  B/s

====== WebDriver manager ======
Current google-chrome version is 90.0.4430
Get LATEST driver version for 90.0.4430
Driver [C:\Users\Chike\.wdm\drivers\chromedriver\win32\90.0.4430.24\chromedriver.exe] found in cache


...

2021-04-21


Test:  99% [000000000000000000000000000000000000000 ] ETA:  0:00:06   0.15  B/s

====== WebDriver manager ======
Current google-chrome version is 90.0.4430
Get LATEST driver version for 90.0.4430
Driver [C:\Users\Chike\.wdm\drivers\chromedriver\win32\90.0.4430.24\chromedriver.exe] found in cache


2021-04-22


Test: 100% [000000000000000000000000000000000000000] Time: 13:54:36   0.15  B/s


Time Wind       Condition Temperature_Fahrenheit Dew_Point_Fahrenheit  \
0    1:00 AM    S          Cloudy                     36                   36   
2    2:00 AM   SW          Cloudy                     38                   38   
3    3:00 AM  SSW  Cloudy / Windy                     37                   34   
5    4:00 AM   SW  Cloudy / Windy                     36                    0   
7    5:00 AM   SW  Cloudy / Windy                     36                    0   
..       ...  ...             ...                    ...                  ...   
30   7:00 PM  WNW   Mostly Cloudy                     39                   16   
31   8:00 PM    W   Partly Cloudy                     39                   16   
32   9:00 PM    W   Partly Cloudy                     39                   14   
33  10:00 PM    W   Mostly Cloudy                     39                   16   
34  11:00 PM    W   Mostly Cloudy                     39                   16   

    Humidity_Float Wind_Speed_MPH Wind_Gust_MPH Pressure_IN Precip_IN  \
0             1.00              6             0          29         0   
2             0.97             13             0          29         0   
3             0.87             29            35          29         0   
5             0.87             23             0          29         0   
7             0.87             21            31          29         0   
..             ...            ...           ...         ...       ...   
30            0.39             14            24          29         0   
31            0.39             12             0          29         0   
32            0.36             12             0          29         0   
33            0.39             12            17          29         0   
34            0.39             15            23          29         0   

   Time_Clean        Date  
0    01:00:00  1990-01-01  
2    02:00:00  1990-01-01  
3    03:00:00  1990-01-01  
5    04:00:00  1990-01-01  
7    05:00:00  1990-01-01  
..        ...         ...  
30   19:00:00  2021-04-22  
31   20:00:00  2021-04-22  
32   21:00:00  2021-04-22  
33   22:00:00  2021-04-22  
34   23:00:00  2021-04-22  

[271715 rows x 12 columns]

In [7]:
weather_df

Time Wind       Condition Temperature_Fahrenheit Dew_Point_Fahrenheit  \
0    1:00 AM    S          Cloudy                     36                   36   
2    2:00 AM   SW          Cloudy                     38                   38   
3    3:00 AM  SSW  Cloudy / Windy                     37                   34   
5    4:00 AM   SW  Cloudy / Windy                     36                    0   
7    5:00 AM   SW  Cloudy / Windy                     36                    0   
..       ...  ...             ...                    ...                  ...   
30   7:00 PM  WNW   Mostly Cloudy                     39                   16   
31   8:00 PM    W   Partly Cloudy                     39                   16   
32   9:00 PM    W   Partly Cloudy                     39                   14   
33  10:00 PM    W   Mostly Cloudy                     39                   16   
34  11:00 PM    W   Mostly Cloudy                     39                   16   

    Humidity_Float Wind_Speed_MPH Wind_Gust_MPH Pressure_IN Precip_IN  \
0             1.00              6             0          29         0   
2             0.97             13             0          29         0   
3             0.87             29            35          29         0   
5             0.87             23             0          29         0   
7             0.87             21            31          29         0   
..             ...            ...           ...         ...       ...   
30            0.39             14            24          29         0   
31            0.39             12             0          29         0   
32            0.36             12             0          29         0   
33            0.39             12            17          29         0   
34            0.39             15            23          29         0   

   Time_Clean        Date  
0    01:00:00  1990-01-01  
2    02:00:00  1990-01-01  
3    03:00:00  1990-01-01  
5    04:00:00  1990-01-01  
7    05:00:00  1990-01-01  
..        ...         ...  
30   19:00:00  2021-04-22  
31   20:00:00  2021-04-22  
32   21:00:00  2021-04-22  
33   22:00:00  2021-04-22  
34   23:00:00  2021-04-22  

[271715 rows x 12 columns]

In [8]:
weather_df.to_pickle(file_name)